In [1]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from math import sqrt
from statsmodels.tsa.arima.model import ARIMA
from sklearn.metrics import mean_squared_error

data = pd.read_csv('./finalData.csv')
data.head(610)

Unnamed: 0  NOC  Year  Medal  Event_Count  Cluster1  Cluster2  Cluster3  \
0             0  AFG  1936      0            4         0         0         0   
1             1  AFG  1948      0            2         0         0         0   
2             2  AFG  1956      0            1         0         0         0   
3             3  AFG  1960      0           13         0         0         0   
4             4  AFG  1964      0            8         0         0         0   
..          ...  ...   ...    ...          ...       ...       ...       ...   
605         605  CHN  2020    175          229         0        13         0   
606         606  CHN  2024    184          237         0        15         1   
607         607  CIV  1964      0           10         0         0         0   
608         608  CIV  1968      0            7         0         0         0   
609         609  CIV  1972      0            7         0         0         0   

     Cluster4  Cluster5  Cluster6  Cluster7  Cluster8  Cluster9  \
0           0         0         0         0         0         0   
1           0         0         0         0         0         0   
2           0         0         0         0         0         0   
3           0         0         0         0         0         0   
4           0         0         0         0         0         0   
..        ...       ...       ...       ...       ...       ...   
605        27        31        85        15         0         4   
606        30        39        82         9         0         8   
607         0         0         0         0         0         0   
608         0         0         0         0         0         0   
609         0         0         0         0         0         0   

     Male_Percentage  is_Host?  
0         100.000000       0.0  
1         100.000000       0.0  
2         100.000000       0.0  
3         100.000000       0.0  
4         100.000000       0.0  
..               ...       ...  
605        35.888502       0.0  
606        38.841567       0.0  
607       100.000000       0.0  
608       100.000000       0.0  
609       100.000000       0.0  

[610 rows x 16 columns]

In [2]:
def filter(NOC, factor):
    if factor not in data.columns:
        raise ValueError(f"Column '{factor}' does not exist in the dataset.")
    filtered_data = data[data['NOC'] == NOC]
    time_series = filtered_data.set_index('Year')[factor]
    return time_series

def predict28(NOC, factor, p, d, q):
    #print(NOC, factor)
    history = filter(NOC, factor)
    model = ARIMA(history, order=(p, d, q))  # ARIMA(p=5, d=1, q=0) with the most recent data
    try:
        model_fit = model.fit()
        next_prediction = model_fit.forecast().item()
        return next_prediction
    except IndexError:
        return 0
    except ValueError:
        return 0 
    
#predict28("AIN", "Male_Percentage", 2, 1, 0)
filter("YMD", "Medal")


Year
1988    0
Name: Medal, dtype: int64

In [3]:
nocs = data["NOC"].unique()
nocs

array(['AFG', 'AHO', 'AIN', 'ALB', 'ALG', 'AND', 'ANG', 'ANT', 'ANZ',
       'ARG', 'ARM', 'ARU', 'ASA', 'AUS', 'AUT', 'AZE', 'BAH', 'BAN',
       'BAR', 'BDI', 'BEL', 'BEN', 'BER', 'BHU', 'BIH', 'BIZ', 'BLR',
       'BOH', 'BOL', 'BOT', 'BRA', 'BRN', 'BRU', 'BUL', 'BUR', 'CAF',
       'CAM', 'CAN', 'CAY', 'CGO', 'CHA', 'CHI', 'CHN', 'CIV', 'CMR',
       'COD', 'COK', 'COL', 'COM', 'CPV', 'CRC', 'CRO', 'CRT', 'CUB',
       'CYP', 'CZE', 'DEN', 'DJI', 'DMA', 'DOM', 'ECU', 'EGY', 'EOR',
       'ERI', 'ESA', 'ESP', 'EST', 'ETH', 'EUN', 'FIJ', 'FIN', 'FRA',
       'FRG', 'FSM', 'GAB', 'GAM', 'GBR', 'GBS', 'GDR', 'GEO', 'GEQ',
       'GER', 'GHA', 'GRE', 'GRN', 'GUA', 'GUI', 'GUM', 'GUY', 'HAI',
       'HKG', 'HON', 'HUN', 'INA', 'IND', 'IOA', 'IRI', 'IRL', 'IRQ',
       'ISL', 'ISR', 'ISV', 'ITA', 'IVB', 'JAM', 'JOR', 'JPN', 'KAZ',
       'KEN', 'KGZ', 'KIR', 'KOR', 'KOS', 'KSA', 'KUW', 'LAO', 'LAT',
       'LBA', 'LBN', 'LBR', 'LCA', 'LES', 'LIB', 'LIE', 'LTU', 'LUX',
       'MAD', 'MAL',

In [4]:
factors = ['Medal', 'Event_Count', 'Cluster1', 'Cluster2', 'Cluster3', 'Cluster4', 'Cluster5', 'Cluster6', 'Cluster7', 'Cluster8', 'Cluster9', 'Male_Percentage']
data28 = pd.DataFrame(index = nocs, columns = factors)

factor = 'Medal'
for noc in nocs:
    data28.loc[noc, factor] = predict28(noc, factor, 0, 1, 0)

factor = 'Event_Count'
for noc in nocs:
    data28.loc[noc, factor] = predict28(noc, factor, 2, 1, 0)

factor = 'Cluster1'
for noc in nocs:
    data28.loc[noc, factor] = predict28(noc, factor, 0, 1, 0)

factor = 'Cluster2'
for noc in nocs:
    data28.loc[noc, factor] = predict28(noc, factor, 0, 2, 6)

factor = 'Cluster3'
for noc in nocs:
    data28.loc[noc, factor] = predict28(noc, factor, 0, 1, 7)

factor = 'Cluster4'
for noc in nocs:
    data28.loc[noc, factor] = predict28(noc, factor, 3, 0, 0)

factor = 'Cluster5'
for noc in nocs:
    data28.loc[noc, factor] = predict28(noc, factor, 0, 2, 6)

factor = 'Cluster6'
for noc in nocs:
    data28.loc[noc, factor] = predict28(noc, factor, 0, 1, 1)

factor = 'Cluster7'
for noc in nocs:
    data28.loc[noc, factor] = predict28(noc, factor, 0, 3, 6)

factor = 'Cluster8'
for noc in nocs:
    data28.loc[noc, factor] = predict28(noc, factor, 0, 1, 7)

factor = 'Cluster9'
for noc in nocs:
    data28.loc[noc, factor] = predict28(noc, factor, 0, 2, 6)

factor = 'Male_Percentage'
for noc in nocs:
    data28.loc[noc, factor] = predict28(noc, factor, 2, 1, 1)

print(data28)

/home/codespace/.python/current/lib/python3.12/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided. As a result, forecasts cannot be generated. To use the model for forecasting, use one of the supported classes of index.
  self._init_dates(dates, freq)
/home/codespace/.python/current/lib/python3.12/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided. As a result, forecasts cannot be generated. To use the model for forecasting, use one of the supported classes of index.
  self._init_dates(dates, freq)
/home/codespace/.python/current/lib/python3.12/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided. As a result, forecasts cannot be generated. To use the model for forecasting, use one of the supported classes of index.
  self._init_dates(dates, freq)
/home/codespace/.python/current/lib/python3.12/site-packages/statsmodels/tsa/base/tsa_model.py

/home/codespace/.python/current/lib/python3.12/site-packages/statsmodels/tsa/base/tsa_model.py:837: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
/home/codespace/.python/current/lib/python3.12/site-packages/statsmodels/tsa/base/tsa_model.py:837: FutureWarning: No supported index is available. In the next version, calling this method in a model without a supported index will result in an exception.
  return get_prediction_index(
/home/codespace/.python/current/lib/python3.12/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided. As a result, forecasts cannot be generated. To use the model for forecasting, use one of the supported classes of index.
  self._init_dates(dates, freq)
/home/codespace/.python/current/lib/python3.12/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided. As a res

    Medal Event_Count Cluster1  Cluster2 Cluster3  Cluster4  Cluster5  \
AFG   0.0    4.556621      0.0       0.0      0.0  0.086024       0.0   
AHO   0.0    6.771586      0.0       0.0      0.0 -0.000005       0.0   
AIN  10.0         NaN      0.0       0.0      0.0         0       0.0   
ALB   2.0    6.219996      0.0       0.0      0.0 -0.000005       0.0   
ALG   7.0   46.252634      0.0  6.000015      0.0 -0.000005       0.0   
..    ...         ...      ...       ...      ...       ...       ...   
YEM   0.0    2.873765      0.0       0.0      0.0 -0.000005       0.0   
YMD   0.0         NaN      0.0       0.0      0.0         0       0.0   
YUG  22.0   59.319364      0.0  4.111962      0.0  0.021066       0.0   
ZAM   1.0    6.045803      0.0       0.0      0.0 -0.000005       0.0   
ZIM   0.0    4.673346      0.0       0.0      0.0 -0.000005 -0.523001   

      Cluster6   Cluster7 Cluster8  Cluster9 Male_Percentage  
AFG        0.0        0.0      0.0       0.0       57.053277

/home/codespace/.python/current/lib/python3.12/site-packages/statsmodels/tsa/base/tsa_model.py:837: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
/home/codespace/.python/current/lib/python3.12/site-packages/statsmodels/tsa/base/tsa_model.py:837: FutureWarning: No supported index is available. In the next version, calling this method in a model without a supported index will result in an exception.
  return get_prediction_index(
/home/codespace/.python/current/lib/python3.12/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided. As a result, forecasts cannot be generated. To use the model for forecasting, use one of the supported classes of index.
  self._init_dates(dates, freq)
/home/codespace/.python/current/lib/python3.12/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided. As a res

In [5]:
data28['is_Host?'] = 0

In [6]:
data28.to_csv("data28.csv")

In [7]:
da

NameError: name 'da' is not defined